# Analyzing The Wanderers

This notebook analyzes the ["The Wanderers"](https://wanderers.ai/) NFT collection with a focus on their traits and the prices they can realize. [Visit the repository](https://github.com/ymyke) for more notebooks on other projects, to use the code, or to contribute.

Important: This notebook uses [Plotly](https://plotly.com/python/) mostly to visualize data. Plotly charts won't be rendered in Githubs notebook viewer. So please [view this notebook on nbviewer](https://nbviewer.org/github/ymyke/niftylytics/blob/main/the_wanderers.ipynb) (or on your local installation after cloning the repo). Note that nbviewer caches notebooks and sometimes takes a long time to pick up a new version.

On the upside, all the Plotly charts are interactive. You can zoom, hover, pan, etc. Zooming is especially important due to the outliers in some the data so you can zoom in on the interesting parts.

Note also that the Plotly charts take a long time to load in the browser because there are a lot of charts with many data points.

In [1]:
import plotly.io as pio
pio.renderers.default = "notebook_connected"

## Get the assets

Note that this takes a long time, i.e. up to 10 minutes. Also note the timestamp below,
that is when the information was last retrieved.

In [2]:
import datetime
from opensea import retrieve_assets

ids = list(range(0, 8888))
assets = retrieve_assets(token_ids=ids, contract="0x8184a482A5038B124d933B779E0Ea6e0fb72F54E")
print(datetime.datetime.now())


............................................................................................................................................................................................................................................................................................................................................................................................................................................................. -- All 8888 assets retrieved.
2021-10-15 13:04:20.728124


## Build a dataframe

Check the trait types there are. We'll see that 1) different assets can have different numbers of traits, 2) the same asset can have traits with the same name, i.e. "Celestial Body".

In [3]:
[", ".join(t["trait_type"] for t in a["traits"]) for a in assets][:10]

['Planet, Anomaly, Music, Cockpit, Left Arm, Window, Celestial Body, Celestial Body, Panel 3, Ships, Right Arm, Panel 4, Panel 2',
 'Planet, Cockpit, Left Arm, Right Arm, Window, Celestial Body, Music, Panel 1, Celestial Body',
 'Window, Left Arm, Music, Panel 2, Cockpit, Right Arm, Panel 4, Planet, Celestial Body',
 'Panel 2, Left Arm, Panel 1, Panel 3, Panel 4, Cockpit, Music, Window, Right Arm, Celestial Body',
 'Anomaly, Panel 5, Ships, Cockpit, Right Arm, Celestial Body, Window, Music, Left Arm',
 'Panel 4, Celestial Body, Window, Celestial Body, Right Arm, Cockpit, Music, Panel 5, Left Arm',
 'Panel 1, Panel 4, Cockpit, Right Arm, Ships, Window, Music, Left Arm, Panel 3',
 'Cockpit, Panel 3, Panel 4, Right Arm, Panel 5, Music, Window, Left Arm',
 'Cockpit, Right Arm, Left Arm, Panel 1, Ships, Panel 5, Window, Music',
 'Panel 4, Ships, Right Arm, Planet, Panel 3, Cockpit, Left Arm, Window, Celestial Body, Music, Celestial Body']

All the possible celestial bodies there are:

In [4]:
set([t["value"]  for a in assets for t in a["traits"] if t["trait_type"] == "Celestial Body"])

{'Blue Galaxy',
 'Blue Stars',
 'Green Stars',
 'Large Green Galaxy',
 'Large Purple Galaxy',
 'Purple Galaxy',
 'Purple Stars',
 'Red Stars'}

We will count the number of Celestial Bodies as well as the number of stars and galaxies when tabulating all the information into a dataframe:

(Large vs not large galaxies will be ignored; could be added as some point in the future.)

In [5]:
import numpy as np
import pandas as pd
import helpers
df, traits = helpers.turn_assets_into_df_wanderers_variant(assets)
hoverdata = [ "Name", *traits, "Probscore"]

In [6]:
assert set(df.LPsymbol.unique()) == set(["ETH", "WETH", np.nan]), """
This sheet does not do currency conversion at the moment and therefore 
assumes all prices are in (W)ETH. But there are more symbols in the input 
data which would lead to apples being compared to ranges below. Aborting.
"""

## How many pieces have a last price on OpenSea?

In [7]:
print(f"{df[~df.Lastprice.isna()].shape[0] / df.shape[0]:.0%}")

77%


## How are prices evolving over time?

Note that this only takes into account the last sale of each piece.

In [8]:
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt

plt.rcParams["figure.figsize"] = (20, 8)
pd.plotting.register_matplotlib_converters()

fig = px.scatter(df, x="LPdate", y="Lastprice", hover_data=hoverdata)
fig.show()

## Price levels today

In [9]:
fig = px.histogram(df, x="Lastprice", marginal="box", hover_data=hoverdata)
fig.show()

## How frequent are the different traits?

In [10]:
pd.set_option("display.max_columns", None)

from IPython.display import display
for trait in sorted(traits.keys()):
    display(
        pd.DataFrame(df[trait].value_counts(normalize=False, sort=True, ascending=True)).transpose()
    )


Monolith  Purple Wormhole  Glitch Wormhole  White Wormhole  \
Anomaly        63              231              237             239   

         Blue Wormhole  Pink Wormhole     -  
Anomaly            254            256  7608

6  5   4    3     2     0     1
Celestial Bodies  2  9  99  522  1884  2928  3444

Cat    -  Glyphs  Hexagon  Sound  Dots  Chart  Falcon  Retro  \
Cockpit   82  139     173      665    678   697    702     704    706   

         Circles  Target  Dotface  Pink  Radar  Planet  
Cockpit      718     718      724   724    725     733

3    2     1     0
Galaxies  31  308  2391  6158

Joint  ETH  Skull  Porn  Jar Eyes  Jar Shrooms  Alien Joint  Hotdog  \
Left Arm     24   33     34    36        36           39           42      44   

          Robo Charge  Goldfish  Bong  Whiskey  8-Ball  Takeout  Banana  \
Left Arm           44        66    81       83      84       86      87   

          Syringe  Watch  Pizza  Chicken  Jar  Orbit  Hook  Coffee  Booze  \
Left Arm       89     89     89       89   90     90    90      92     92   

          Knife  Bone  Egg  Flag  Burn  Boba  Laser  Flower  Shrooms  Wine  \
Left Arm     93    94   98    98    99   100    106     106      106   106   

          Zombie    -  Treasure  Slider  V Steering  Shifter  Tablet  \
Left Arm     112  139       338     346         365      367     370   

          Hologram  Handcrank  Antennae  Thrust  Big Button  \
Left Arm       371        375       376     379         380   

          Button Row Slider  Swipe  Buttons  Alien Gearshift  Button Row  \
Left Arm                384    384      390              390         393   

          Gearshift  
Left Arm        394

...

Joint  ETH  Jar Shrooms  Skull  Hotdog  Porn  Alien Joint  \
Right Arm     29   31           32     36      39    40           40   

           Jar Eyes  Robo Charge  Knife  Jar  Flag  Bong  8-Ball  Orbit  \
Right Arm        40           40     78   78    82    82      84     84   

           Pizza  Banana  Zombie  Bone  Egg  Boba  Syringe  Whiskey  Takeout  \
Right Arm     87      88      88    89   95    95       97       98      100   

           Hook  Wine  Coffee  Laser  Booze  Watch  Shrooms  Goldfish  Burn  \
Right Arm   100   100     100    102    104    104      104       106   107   

           Chicken  Flower    -  Alien Gearshift  Handcrank  Hologram  Slider  \
Right Arm      108     108  139              315        328       332     346   

           Swipe  Buttons  Tablet  Button Row Slider  V Steering  Gearshift  \
Right Arm    361      374     374                377         382        383   

           Antennae  Shifter  Thrust  Big Button  Treasure  Button Row  
Right Arm       389      390     392         394       403         414

Space Station  Guardian (active)  Large Battle  Cargo  Flyby Trio  \
Ships            144                155           157    171         174   

       Guardian (rogue)  Battle (alt)  Triforce  Flyby Dogfight  UFO  \
Ships               175           178       186             186  188   

       Destroyed Freighter  Flyby  Battle  Fleet  Docking  Freighter  \
Ships                  188    189     189    193      194        195   

       Freighter Battle     -  
Ships               209  5817

4    3     2     1     0
Stars  6  156  1095  3449  4182

-  Tubes  Eyes  ETH  Plants  Blue  Screens  Green  White  Bolt  \
Window  139    184   196  215     428   724      735    755    767   773   

        Crack  Wires  Purple  Pink  Dice  
Window    779    781     784   802   826

Guardian Marked, RADIOACTIVE  Warp Squad Sixteen  Guardian Marked  \
special                             1                  16               40   

         RADIOACTIVE     -  
special           82  8749

## How much do people pay for the different traits?

**Some Observations**:

- The monolith anomaly commands much higher prices than other anomalies. It is also the most seldom anomaly.
- The more celestial bodies, the higher the price. Same with galaxies and stars. (4 stars is really seldom and outperforms 0-3 stars massively.)
- A cat cockpit slightly outperforms other cockpits. Interestingly, glyphs perform average, even though they are much rarer than average. No cockpit at all has a bad impact on price.
- Arms: Joints perform best, followed by ETH, bong, porn, alien joint, and skull. Flag is clearly worst (I wonder why?). Bongs perform much better than their rarity would suggest, whereas flags left perform much worse than their rarity would suggest (not so much for flags right, strangely).
- Music doesn't make a difference. Except no music at all, which is detrimental to price.
- Panels: Crypto, bounty, tetris, spam are the best preformers which is very much in line with their rarity.
- Planet: Anger orb and destroyed planet are clearly performing best and also rarest.
- Ships: Doesn't make much of a difference.
- Window: Doesn't make much of a difference.
- Special: Specials in general add to the value. Warp squad sixteen performs very high.
- Keep in mind that this doesn't take into account possible cross-correlations between the different traits. 


In [11]:
for trait in sorted(traits.keys()):

    fig = go.Figure()

    for traitvariant in (
        df.groupby(trait).median().sort_values("Lastprice", ascending=False).index
        ):
        fig.add_trace(
            go.Box(
                y=df[df[trait] == traitvariant].fillna("-").Lastprice.values,
                name=traitvariant,
                # boxpoints="all",
                jitter=0.2,
                whiskerwidth=0.2,
                marker_size=2,
                line_width=1,
            )
        )
    fig.update_layout(title=trait)
    fig.show()

## What is pricier, galaxies or stars?

There seems to be no fundamental difference between stars and galaxies. In either case, rarity is the differentiator: 3 galaxies is slightly rare, 4 stars is rare, 5 bodies overall is rare and 6 bodies is superrare – so these all command higher prices.

In [12]:
df["Celestialstype"] = df.apply(
    lambda x: "Starsonly"
    if x["Galaxies"] == 0
    else "Galaxiesonly"
    if x["Stars"] == 0
    else "Both",
    axis=1,
)
px.box(df, x="Celestial Bodies", y="Lastprice", color="Celestialstype", points="all", hover_data=hoverdata)

## Check if there's a bargain for any of the more lucrative traits

In [13]:
display(df[df["Anomaly"] != "-"].sort_values("Price").head(3))
display(df[df["Celestial Bodies"] >= 4].sort_values("Price").head(3))
display(df[df["Left Arm"].isin(["Joint", "Alien Joint", "Bong", "Skull", "Porn", "ETH"])].sort_values("Price").head(3))
# ...

Name  Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                             
7078  7078  0.640     ETH      0.579      ETH 2021-09-29 01:36:42   0.009378   
4430  4430  0.649     ETH      0.480      ETH 2021-10-06 15:21:48   2.611375   
5942  5942  0.690     ETH      0.490      ETH 2021-10-03 20:29:36   0.001869   

              Anomaly  Celestial Bodies Cockpit  Galaxies         Left Arm  \
ID                                                                           
7078    Pink Wormhole                 0  Falcon         0  Alien Gearshift   
4430   White Wormhole                 0   Chart         0         Antennae   
5942  Purple Wormhole                 1   Radar         1             Bone   

             Music Panel 1    Panel 2            Panel 3 Panel 4     Panel 5  \
ID                                                                             
7078  The Wayfarer       -  Particles              Noisy       -  Spacecraft   
4430  The Wayfarer       -          -                  -    Data           -   
5942   The Cruiser       -          -  Pulselights (alt)  Mosaic        Code   

     Planet Right Arm                Ships  Stars Window special  \
ID                                                                 
7078      -   Shifter  Destroyed Freighter      0   Dice       -   
4430      -    Thrust                    -      0   Dice       -   
5942      -    Banana                    -      0   Bolt       -   

                                                   Link Celestialstype  
ID                                                                      
7078  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
4430  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
5942  https://opensea.io/assets/0x8184a482a5038b124d...   Galaxiesonly

Name  Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                             
3686  3686   0.85     ETH      0.210      ETH 2021-08-26 14:17:05   0.042166   
1382  1382   1.00     ETH      0.325      ETH 2021-09-15 13:10:35   0.236804   
1686  1686   1.00     ETH        NaN      NaN                 NaT   0.523046   

     Anomaly  Celestial Bodies Cockpit  Galaxies Left Arm           Music  \
ID                                                                          
3686       -                 4   Chart         2   Thrust    The Ponderer   
1382       -                 4   Sound         1   Thrust  Cosmic Drifter   
1686       -                 4   Sound         1    Swipe  Lone Planeteer   

     Panel 1 Panel 2            Panel 3       Panel 4 Panel 5      Planet  \
ID                                                                          
3686       -  Bricks  Pulselights (alt)           DNA       -           -   
1382  Static       -         Spacecraft             -       -  Large Ring   
1686       -       -               JPEG  Tunnel (alt)    JPEG           -   

     Right Arm   Ships  Stars Window special  \
ID                                             
3686  Hologram  Battle      2   Pink       -   
1382   Syringe       -      3   Dice       -   
1686  Antennae       -      3   Pink       -   

                                                   Link Celestialstype  
ID                                                                      
3686  https://opensea.io/assets/0x8184a482a5038b124d...           Both  
1382  https://opensea.io/assets/0x8184a482a5038b124d...           Both  
1686  https://opensea.io/assets/0x8184a482a5038b124d...           Both

Name  Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                             
5357  5357    1.0     ETH        0.6      ETH 2021-10-04 20:58:54   0.004795   
734    734    1.0     ETH        NaN      NaN                 NaT   0.083415   
750    750    1.0     ETH        NaN      NaN                 NaT   0.022772   

     Anomaly  Celestial Bodies  Cockpit  Galaxies     Left Arm         Music  \
ID                                                                             
5357       -                 1  Hexagon         0         Bong  The Wayfarer   
734        -                 2   Target         0         Bong   Space Ender   
750        -                 0   Falcon         0  Alien Joint   The Cruiser   

     Panel 1       Panel 2        Panel 3        Panel 4 Panel 5 Planet  \
ID                                                                        
5357  Spiral  Transmission      Pink Data  Radial Static       -      -   
734   Tunnel             -  Radial Static  Radial Points       -      -   
750     Trim  Transmission              -        Sliders       -      -   

       Right Arm Ships  Stars Window special  \
ID                                             
5357  V Steering     -      1  Crack       -   
734      Shifter     -      2  Green       -   
750   V Steering     -      0   Dice       -   

                                                   Link Celestialstype  
ID                                                                      
5357  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
734   https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
750   https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly